<a href="https://colab.research.google.com/github/Mafaz03/ReditScraper/blob/main/analysis_v2.ipynb" target="_parent"><img src="https://colab.research.google.com/assets/colab-badge.svg" alt="Open In Colab"/></a>

In [4]:
!pip install -q praw
from datetime import datetime
import pandas as pd
%matplotlib inline
import matplotlib.pyplot as plt
import seaborn as sb
import praw
import pandas as pd
from tqdm import tqdm
import requests
from PIL import Image
from torchvision import transforms
from io import BytesIO
import numpy as np
import seaborn as sns

In [5]:
pd.set_option('display.max_rows', None)

In [6]:
import warnings
warnings.filterwarnings("ignore")

In [7]:
reddit = praw.Reddit(client_id = "",
            client_secret = "",
            username = "",
            password = "",
            redirect_uri = "http://localhost:8080",
            user_agent = "",
            check_for_async=False)


In [8]:
def scrape_reddit(subreddit: str, limit = 10, sortby = 'year', show_safe = None):
  sub = reddit.subreddit(subreddit)
  result = []
  sub_itter = sub.top(sortby,limit = limit)
  for submission in tqdm(sub_itter):
    d = {}
    d['id'] = submission.id
    d['title'] = submission.title
    d['num_comments'] = submission.num_comments
    d['score'] = submission.score
    d['upvote_ratio'] = submission.upvote_ratio
    d['date'] = datetime.fromtimestamp(submission.created_utc)
    d['domain'] = submission.domain
    d['nsfw'] = submission.over_18
    try: d['image'] = submission.preview["images"][0]["source"]["url"]
    except: d['image'] = None
    try: d['author'] = submission.author.name
    except: d['author'] = 'Not Found'
    if show_safe == True and d['nsfw'] == True: d={}
    if show_safe == False and d['nsfw'] == False: d={}
    result.append(d)
  result = [item for item in result if item]
  return pd.DataFrame(result)

In [20]:
def show_images(links_, title = None, figsize=(15,15), sub_title=None, noframe=True, max_col = 6, max_size=500, max_images = None, fontsize = 10, **kwargs):
  transform = transforms.ToTensor()
  if isinstance(links_, str): links = [links_]
  if max_images: num_images = min(len(links_), max_images)
  else: num_images = len(links_)
  num_rows = (num_images - 1) // max_col + 1
  fig, axes = plt.subplots(num_rows, max_col, figsize=figsize)
  if num_images > 1: axes = axes.flatten()
  if sub_title:
    if isinstance(sub_title, list) and len(sub_title) == num_images: pass
    elif isinstance(sub_title, str): sub_title = [sub_title] * num_images
    else: sub_title = [''] * num_images
  failed = 0
  links = []
  for link in links_:
    if link is not None:
      links.append(link)
    else: failed+=1
  if max_images and len(links)<= max_images:
    for link in links_:
      if link not in links_: links.append(link)
      if len(links) == max_images: break
  links = links[:num_images]
  print(f"Displaying {len(links)} images in total")
  for i, link in enumerate(links):
    try:
      response = requests.get(link)
      image = Image.open(BytesIO(response.content))
      image.thumbnail((max_size, max_size), Image.LANCZOS)
      if image.mode != 'RGB': image = image.convert('RGB')
      img_tensor = transform(image)
      if img_tensor.shape[0] == 3: img_tensor = img_tensor.permute(1, 2, 0)
      np_image = np.array(img_tensor)
      if sub_title:
        word = sub_title[i] if len(sub_title[i]) <= 45 else ""
        axes[i].set_title(word, fontsize = fontsize)
      axes[i].imshow(np_image, **kwargs)
    except: pass
    if noframe: axes[i].axis('off')
  for j in range(i + 1, num_rows * max_col):
      axes[j].axis('off')
  if title: plt.suptitle(title)
  print(f"{failed} post did not have images, or failed to fetch")
  plt.tight_layout()
  plt.show()

In [41]:
subreddit = "photos"
result = scrape_reddit(subreddit, limit = 100, sortby = "year", show_safe = None)

100it [00:08, 11.58it/s]


In [42]:
show_images(list(result.image), figsize = (20,20), max_size = 5000, max_col = 5, max_images=25) # Can view single image

Displaying 25 images in total
28 post did not have images, or failed to fetch
